# Folium

Testing ground for creating choropleths with our ward/FSA geojsons

In [1]:
import folium

In [2]:
m = folium.Map(location=[43.64448905083427, -79.3821119760047])
m

In [4]:
import requests

# Toronto Open Data is stored in a CKAN instance. It's APIs are documented here:
# https://docs.ckan.org/en/latest/api/

# To hit our API, you'll be making requests to:
base_url = "https://ckan0.cf.opendata.inter.prod-toronto.ca"

# Datasets are called "packages". Each package can contain many "resources"
# To retrieve the metadata for this package and its resources, use the package name in this page's URL:
url = base_url + "/api/3/action/package_show"
params = {"id": "city-wards"}
package = requests.get(url, params=params).json()

# To get resource data:
for idx, resource in enumerate(package["result"]["resources"]):
    # for datastore_active resources:
    if resource["datastore_active"]:
        # To get all records in CSV format:
        url = base_url + "/datastore/dump/" + resource["id"]
        resource_dump_data = requests.get(url).text
        # print(resource_dump_data)

        # To selectively pull records and attribute-level metadata:
        url = base_url + "/api/3/action/datastore_search"
        p = {"id": resource["id"]}
        resource_search_data = requests.get(url, params=p).json()["result"]
        # print(resource_search_data)
        # This API call has many parameters. They're documented here:
        # https://docs.ckan.org/en/latest/maintaining/datastore.html

    # To get metadata for non datastore_active resources:
    if not resource["datastore_active"]:
        url = base_url + "/api/3/action/resource_show?id=" + resource["id"]
        resource_metadata = requests.get(url).json()
        print(resource_metadata["result"]["name"])
        # From here, you can use the "url" attribute to download this file

25-ward-model-december-2018-wgs84-latitude-longitude
44-ward-model-may-2010-wgs84-latitude-longitude
47-ward-model-wgs84-latitude-longitude
44-ward-model-oct-2009-mtm-3-degree-zone-10-nad27
44-ward-model-may-2010-mtm-3-degree-zone-10-nad27
City Wards Data - 4326.gpkg
City Wards Data - 2945.gpkg
City Wards Data - 4326.csv
City Wards Data - 2945.csv
City Wards Data - 4326.geojson
City Wards Data - 2945.geojson
City Wards Data - 4326.zip
City Wards Data - 2945.zip
City Wards Data - 2952.gpkg
City Wards Data - 2952.geojson
City Wards Data - 2952.csv
City Wards Data - 2952.zip


In [5]:
city_wards = "../data/city-wards-boundary.geojson"
folium.GeoJson(data=city_wards, name="geojson").add_to(m)
m

In [6]:
import pandas as pd

In [8]:
rentals = pd.read_csv("../data/notebooks/short-term-rental-registrations-data.csv")
rentals.dtypes

_id                               int64
operator_registration_number     object
postal_code                      object
ward_number                     float64
ward_name                        object
dtype: object

In [9]:
rental_count = rentals.groupby("ward_name").size()
rental_count

ward_name
Beaches-East York            278
Davenport                    414
Don Valley East               89
Don Valley North             153
Don Valley West              114
Eglinton-Lawrence            133
Etobicoke Centre             142
Etobicoke North               97
Etobicoke-Lakeshore          270
Humber River-Black Creek     107
Parkdale-High Park           317
Scarborough Centre            97
Scarborough North             56
Scarborough Southwest        170
Scarborough-Agincourt         91
Scarborough-Guildwood         86
Scarborough-Rouge Park        92
Spadina-Fort York           1810
Toronto Centre               595
Toronto-Danforth             358
Toronto-St. Paul's           215
University-Rosedale          512
Willowdale                   253
York Centre                  122
York South-Weston            156
dtype: int64

In [10]:
folium.Choropleth(
    geo_data=city_wards,
    name="choropleth",
    data=rental_count,
    # columns=[''] # passing a series, so no need to specify columns
    key_on="feature.properties.AREA_NAME",
    fill_color="YlGn",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Short term rentals",
).add_to(m)
folium.LayerControl().add_to(m)
m

The `key_on` feature refers to the variable in the geojson file for our `series` to bind to. Strangely, even though the json has `features`, the above only runs if I use `feature`. The [docs state that this argument *must start with `feature`*](https://python-visualization.github.io/folium/modules.html?highlight=choropleth#folium.features.Choropleth)

So `city-wards-fsa.geojson` is okay. Let's test `toronto_fsa`

In [11]:
fsa_m = folium.Map(location=[43.64448905083427, -79.3821119760047])

# fetch url
url_pop = "https://www12.statcan.gc.ca/census-recensement/2016/dp-pd/hlt-fst/pd-pl/Tables/CompFile.cfm?Lang=Eng&T=1201&OFT=FULLCSV"

# read into dataframe
pop = pd.read_csv(url_pop)
pop.head()

Geographic code Geographic name      Province or territory  \
0              01          Canada                        NaN   
1             A0A             A0A  Newfoundland and Labrador   
2             A0B             A0B  Newfoundland and Labrador   
3             A0C             A0C  Newfoundland and Labrador   
4             A0E             A0E  Newfoundland and Labrador   

  Incompletely enumerated Indian reserves and Indian settlements, 2016  \
0                                                  T                     
1                                                NaN                     
2                                                NaN                     
3                                                NaN                     
4                                                NaN                     

   Population, 2016  Total private dwellings, 2016  \
0        35151728.0                     15412443.0   
1           46587.0                        26155.0   
2           19792.0                        13658.0   
3           12587.0                         8010.0   
4           22294.0                        12293.0   

   Private dwellings occupied by usual residents, 2016  
0                                         14072079.0    
1                                            19426.0    
2                                             8792.0    
3                                             5606.0    
4                                             9603.0

In [12]:
# again, all FSAs starting with "M" are in toronto, with a few exceptions in mississauga
pop_to = pop[pop["Geographic code"].str.contains(r"M\d\w")][
    ["Geographic code", "Population, 2016"]
]
pop_to

Geographic code  Population, 2016
895             M1B           66108.0
896             M1C           35626.0
897             M1E           46943.0
898             M1G           29690.0
899             M1H           24383.0
..              ...               ...
992             M9N           25074.0
993             M9P           20874.0
994             M9R           33743.0
995             M9V           55959.0
996             M9W           40684.0

[102 rows x 2 columns]

In [15]:
to_fsa = "../data/toronto_fsa.geojson"
folium.Choropleth(
    geo_data=to_fsa,
    name="choropleth",
    data=pop_to,
    columns=["Geographic code", "Population, 2016"],  # passing a df, specify [key, val]
    key_on="feature.properties.CFSAUID",
    fill_color="YlGn",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Population",
).add_to(fsa_m)
folium.LayerControl().add_to(fsa_m)
fsa_m